In [2]:
import sys
sys.path.insert(0,'..')

In [5]:
import random

import numpy as np
import torch
from torch import nn
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import RBF, DotProduct, WhiteKernel
from priors.utils import get_batch_to_dataloader

In [68]:
def get_gp():
    gp = GaussianProcessRegressor(
            kernel=RBF(length_scale=.6, length_scale_bounds='fixed'),
            random_state=0, optimizer=None)
    return gp

In [77]:
seq_len = 4
num_features = 10
x = torch.rand(seq_len, num_features)
gpr = get_gp()
y = gpr.sample_y(x, random_state=random.randint(0, 2 ** 32)).squeeze()


In [78]:
for num_copies in range(1,20):
    gp = get_gp()
    x_copied = x.tile((1,num_copies))
    gp.fit(x_copied[:-1],y[:-1])
    m,s = gp.predict(x_copied[-1].reshape(1,-1), return_std=True)
    print(m,s)

[-0.29995838] [0.90399136]
[-0.1039504] [0.98874968]
[-0.03414801] [0.99876344]
[-0.01104748] [0.99986603]
[-0.00356252] [0.9999855]
[-0.00114827] [0.99999843]
[-0.00037014] [0.99999983]
[-0.00011934] [0.99999998]
[-3.8486538e-05] [1.]
[-1.24147253e-05] [1.]
[-4.00568455e-06] [1.]
[-1.2927993e-06] [1.]
[-4.17353027e-07] [1.]
[-1.34771328e-07] [1.]
[-4.35327732e-08] [1.]
[-1.40657691e-08] [1.]
[-4.54613576e-09] [1.]
[-1.46979425e-09] [1.]
[-4.75345491e-10] [1.]


In [79]:
k = RBF(length_scale=.6, length_scale_bounds='fixed')
k(x)

array([[1.        , 0.1047567 , 0.17720387, 0.33463634],
       [0.1047567 , 1.        , 0.14686013, 0.04858264],
       [0.17720387, 0.14686013, 1.        , 0.32035965],
       [0.33463634, 0.04858264, 0.32035965, 1.        ]])

In [80]:
k = RBF(length_scale=.6, length_scale_bounds='fixed')
k(x_copied)

array([[1.00000000e+00, 2.41799081e-19, 5.26006251e-15, 9.26592960e-10],
       [2.41799081e-19, 1.00000000e+00, 1.48311381e-16, 1.10443925e-25],
       [5.26006251e-15, 1.48311381e-16, 1.00000000e+00, 4.04686299e-10],
       [9.26592960e-10, 1.10443925e-25, 4.04686299e-10, 1.00000000e+00]])